### Tworzenie tabeli d_calendar
Aby uruchomić poniższy kod należy najpierw odmrozić jego zawartość.


In [68]:
from pyspark.sql import functions as F

df = spark.createDataFrame([(1,)], ["id"]).withColumn("date", F.explode(F.expr("sequence(to_date('2000-01-01'), to_date('2024-12-31'), interval 1 day)"))).drop('id')

df = df.withColumn("year",F.concat(F.lit("Y-"),F.year("date")))\
.withColumn("month",F.concat(F.lit("M-"),F.year('date'),F.lpad(F.month("date"),2,'0')))\
.withColumn('dayOfWeek',F.dayofweek('date'))\
.withColumn("id",F.concat(F.lit("D-"),F.year('date'),F.lpad(F.month("date"),2,'0'),F.lpad(F.dayofmonth("date"),2,'0')))\
.select('id','date','year','month','dayOfWeek')

df.write.format('delta').mode('overwrite').saveAsTable('d_calendar')

StatementMeta(, 725867aa-9b80-487a-9bbf-085b75efab6f, 70, Finished, Available, Finished)

### Klasa użytkowa do obsługi połączenia pyODBC

In [5]:
class DatabaseConnection:
    import struct
    from itertools import chain, repeat
    import pyodbc

    def __init__(self, pSqlEndpoint):
        vConnectionString = f"Driver={{ODBC Driver 18 for SQL Server}};Server={pSqlEndpoint},1433;Encrypt=Yes;TrustServerCertificate=No"
        token_object = mssparkutils.credentials.getToken("pbi")
        encoded_bytes = bytes(self.chain.from_iterable(zip(bytes(token_object, "UTF-8"), self.repeat(0))))
        token_bytes = self.struct.pack("<i", len(encoded_bytes)) + encoded_bytes
        attrs_before = {1256: token_bytes}
        vConnection = self.pyodbc.connect(vConnectionString, attrs_before=attrs_before)
        self.cursor = vConnection.cursor()

    def get_query_results(self, pQuery):
        self.cursor.execute(pQuery)
        return self.cursor.fetchall()

StatementMeta(, cb3016c7-6c12-4dc9-ae6a-f74a14b67e01, 7, Finished, Available, Finished)

### Pętla z użyciem pySpark

In [2]:
from datetime import date, timedelta

vStart = date(2024,7,1)
for vDay in [d for d in (vStart + timedelta(n) for n in range(30))]:
    vSql = "select id from d_calendar where date = '{day}'".format(day = vDay)
    vRes = spark.sql(vSql).collect()[0][0]

StatementMeta(, cb3016c7-6c12-4dc9-ae6a-f74a14b67e01, 4, Finished, Available, Finished)

### Utworzenie połączenia pyODBC

In [6]:
dbConn = DatabaseConnection('ordve2dp5nduxpctrlp6b2zx7e-cmehm6ccefoetgd4t2ravzecui.datawarehouse.fabric.microsoft.com','lh_SQLConnectionTest')

StatementMeta(, cb3016c7-6c12-4dc9-ae6a-f74a14b67e01, 8, Finished, Available, Finished)

### Pętla z użyciem pyODBC

In [7]:
from datetime import date, timedelta

vStart = date(2024,7,1)
for vDay in [d for d in (vStart + timedelta(n) for n in range(30))]:
    vSql = "select id from lh_SQLConnectionTest.dbo.d_calendar where date = '{day}'".format(day = vDay)
    vWyn = dbConn.get_query_results(vSql)[0][0]

StatementMeta(, cb3016c7-6c12-4dc9-ae6a-f74a14b67e01, 9, Finished, Available, Finished)